In [14]:
import cadquery as cq

import qrcode
from tqdm import tqdm  # Progress bar for QR generation

## Bodenplatte

In [15]:
# Define the dimensions of the box
base_length = 200.0
base_width = 200.0
base_height = 6.0


def create_socket(text_bottom):
    
    # Define the dimensions of the box
    rand_height = 4
    rand_width = 2.4 #(should be dividable by 0.4, however 2 was not so good) (1.2 war zu duenn!!!)
    fontsize = 12
    fontsize_attribution = 8
    text_depth = 1
    qr_cutout_size = 50  # 40 mm (4 cm)
    qr_cutout_depth = 0.5  # 1 mm deep
    
    font = 'Noto Sans Mono'
    kind = 'bold'
    
    
    # Create the box
    outer_box = cq.Workplane("XY").box(base_length, base_width, base_height + rand_height)
    # Innere Box, um den  zu erzeugen
    inner_box = cq.Workplane("XY").box(base_length - rand_width, base_width - rand_width, rand_height).translate((0,0, - base_height /2))
    # Subtrahiere die innere Box von der äußeren Box, um einen Rand zu erzeugen
    box = outer_box.cut(inner_box)
    
    ## Attribution on top
    attribution = cq.Workplane("XY").text(txt="OpenStreetMap, 2025\n ♥ Touch Mapper",fontsize=fontsize_attribution,distance=10,font=font, kind=kind, halign='right')
    attribution_width = attribution.val().BoundingBox().xmax
    attribution_height = attribution.val().BoundingBox().ymax
    attribution = attribution.translate( (base_length / 2- attribution_width -  fontsize_attribution / 3 , base_width / 2 - attribution_height -  fontsize_attribution / 3, (base_height + rand_height) / 2 - text_depth) )
    box = box.cut(attribution)

    ## Logo on top
    logo = cq.importers.importDXF("TH-Wildau-Logo_HKS44_ohneSchrift_skaliert.dxf").wires().toPending().extrude(10) 
    logo_height = logo.val().BoundingBox().ymax
    logo = logo.translate((-base_width / 2 + 5 ,base_length / 2 -5 -logo_height, (base_height + rand_height) / 2 - text_depth)) 
    box = box.cut(logo)

    # lower text
    text = cq.Workplane("XY").text(txt=text_bottom,fontsize=fontsize,distance=10,font=font, kind=kind)
    text_width = text.val().BoundingBox().xmax
    text = text.translate( (base_length / 2 - text_width -  fontsize / 3 ,-base_width / 2 + fontsize / 3*2, (base_height + rand_height) / 2 - text_depth) )
    
    box = box.cut(text)
    
    # 📌 Cut space (1 mm deep) right **above** the lower text
    qr_cutout_x = base_length / 2 - qr_cutout_size / 2 - rand_width * 5
    qr_cutout_y = -base_width / 2 + rand_width * 22  # Adjusted Y-position above text
    qr_cutout = cq.Workplane("XY").box(qr_cutout_size, qr_cutout_size, qr_cutout_depth).translate(
        (qr_cutout_x, qr_cutout_y, (base_height + rand_height) / 2 - qr_cutout_depth / 2 )
    )
    box = box.cut(qr_cutout)

    return box

In [16]:
# just to check
# needs to be run twice, dont know why??
print_location = 'Präsenzstelle, Luckenwalde'

baseplate = create_socket(print_location)
baseplate

## Legende

In [7]:
# new metrics, assembly to keep in parts (colors get lost by bambu import)


# Function to convert RGBA to RGB and return a Color object
def rgba_to_color(rgba):
    r, g, b, a = rgba  # Ignore the alpha channel
    return cq.Color(r / 255.0, g / 255.0, b / 255.0, a)  # Return a Color object
    


leg_length = 80.0
leg_width = 48.0 #60.0
leg_height = 4.0    # highest buildings 3mm
def create_legend():

    fontsize = 5.5
    text_depth = 0.5
    
    font = 'Noto Sans Mono'
    kind = 'bold'
    box = cq.Workplane("XY").box(leg_length, leg_width, leg_height)

    assy = (
    cq.Assembly(box, color=cq.Color("lightgray"))
    )
    


    # radweg
    ways = [{
                'label': 'Separater Radweg',
                'line_width': 0.85,
                'line_height': 1.5, # height of highway 
                'line_length': 12, 
                #'color': "blue",
                'color': (19, 59, 125, 1),  # dunkel blau

            },
        {
                'label': 'Fahrbahnseitiger\n Radweg',
                'line_width': 2,
                'line_height': 0.85, # height of highway 
                'line_length': 12, 
                #'color': "blue",
                'color': (42, 104, 145, 1),  # marine blau aber heller "#99cbe8" 

            },

            {
                'label': 'Rad erlaubt',
                'line_width': 0.85,
                'line_height': 1.5, # height of highway 
                'line_length': 12, 
                #'color': "blue",
                'color': (48, 210, 213, 1),  # tuerkis

            }#,
           #{
           #     'label': 'Fußgängerzone',
           #     'line_width': 4.5,
           #     'line_height': 1,  # height of cycleway
           #     'line_length': 7, 
           #     #'color': "blue",
           #     'color': (95, 148, 132, 1), # gruen-blau
#
           # }
           ]

    # set initial y_position for text/lines
    y_position_text = leg_width / 2  + 6
    for line, way in enumerate(ways):

        color_rgb=rgba_to_color(way['color'])

        # labels
        text = cq.Workplane("XY").text(txt=way['label'], fontsize=fontsize, distance=text_depth, font=font, kind=kind, halign='right')
        text_width = text.val().BoundingBox().xmax * 2
        text_height = text.val().BoundingBox().ymax * 2    
        #y_position = width / 2 - fontsize * 1.5 * (line +1) + fontsize *.5 
        y_position_text += - fontsize * 2.2 - text_height /2 #+2
        text = text.translate( (leg_length / 2 - text_width -  fontsize / 1.5 , y_position_text  , leg_height / 2 ) )
        #box = box.union(text)
        assy.add(text, color=cq.Color("white"))

        # ways
        way_ = cq.Workplane("XY").box(way['line_length'], way['line_width'], way['line_height'])
        way_ = way_.translate( ( - leg_length /2 + 10 , y_position_text, leg_height / 2 + way['line_height'] / 2) )
        #if way['label']=='Fahrbahnseitiger\n Radweg':
        #        line_witdh_extra=0.5
        #        way_x = cq.Workplane("XY").box(way['line_length'], line_witdh_extra, way['line_height'])
        #        #way_x = way_.translate( ( - leg_length /2 + 10 , y_position_text- (way['line_width'] /2) , leg_height / 2 + way['line_height'] / 2) )
        #        way_x = way_x.translate( ( - leg_length /2 + 10 , y_position_text+ way['line_width'] / 2 + line_witdh_extra / 2 , leg_height / 2 + way['line_height'] / 2) )

        #        #color_rgb=rgba_to_color((42, 122, 36, 1)) # green
        #        assy.add(way_x, color=cq.Color("green"))
            
        #box = box.union(way)
        color_rgb=rgba_to_color(way['color'])
        assy.add(way_, color=color_rgb)


    return(assy)


#assy_legend = create_legend()

#display(assy)

#assy_legend.save("map_legend_v03a.step")

## QR-Code generation

In [8]:


def create_qr_code_flat(size=55, total_thickness=1, data="no"):
    """
    Creates a flat QR code where red QR elements are level with the grey background.
    
    :param size: The width/height of the QR code (square).
    :param total_thickness: The total thickness of both red and grey parts.
    :param data: The text or link for the QR code.
    :return: CadQuery Assembly with a flat QR code.
    """

    # Generate QR code
    qr = qrcode.QRCode(box_size=1, border=4)
    qr.add_data(data)
    qr.make()

    qr_size = len(qr.modules)  # Size of the QR code in pixels
    quiet_zone = 4  # Border around the QR code

    scale_factor = size / (qr_size + 2 * quiet_zone)  # Scale QR code to fit the cutout

    grey_base_model = cq.Workplane("XY").box(size, size, total_thickness)  # Grey base with full thickness
    red_base_model = cq.Workplane("XY")  # Red elements

    # Create QR pattern (Red areas on Grey base)
    for y, row in tqdm(enumerate(qr.modules), total=len(qr.modules), desc="Generating QR Code Layers"):
        for x, module in enumerate(row):
            x_pos = (x - qr_size // 2) * scale_factor
            y_pos = (-y + qr_size // 2) * scale_factor

            if module:  # Red QR Code elements
                red_block = cq.Workplane("XY").box(scale_factor, scale_factor, total_thickness).translate(
                    (x_pos, y_pos, 0)  # Ensure it is perfectly aligned with the grey base
                )
                red_base_model = red_base_model.union(red_block)

    # Cut out the QR pattern from the grey base
    grey_base_model = grey_base_model.cut(red_base_model)

    # Create the final assembly
    qr_assembly = cq.Assembly()
    qr_assembly.add(grey_base_model, name="grey_base", color=cq.Color("lightgray"))
    qr_assembly.add(red_base_model, name="red_base", color=cq.Color("red"))

    return qr_assembly



# show_object(qr_flat)  # Uncomment to visualize in CadQuery


## Assembly

In [9]:
# Get baseplate
print_location = 'Präsenzstelle, Luckenwalde'
qr_data="https://osm.org/go/0MYjvAdAe?m="


baseplate = create_socket(print_location)

# Rotate baseplate
baseplate_ro = baseplate.rotateAboutCenter((0, 1, 0), 180)  # Rotate Y

# Get legend
assy_legend = create_legend()

# Get QR code assembly
#assy_qr = create_qr_code(size=50, data=print_location)  # QR size matches cutout
#assy_qr = create_qr_code_red_only(size=60, data=qr_data)
#assy_qr=qr_flat
# Example usage:
assy_qr = create_qr_code_flat(size=55, data=qr_data)

Generating QR Code Layers: 100%|██████████| 29/29 [00:58<00:00,  2.01s/it]


In [10]:
# to check the qr code only
assy_qr

In [11]:
qr_cutout_size=50
#rand_width = 2.4

# 📌 QR-Cutout Position
#qr_cutout_x = base_length / 2 - qr_cutout_size / 2 - fontsize + 1.5
#qr_cutout_y = -base_width / 2 + fontsize * 4
qr_cutout_x = base_length / 2 - qr_cutout_size / 2 - 10.8 # rand_width * 4.5
qr_cutout_y = -base_width / 2 + 52.8 #+ rand_width * 22  # Adjusted Y-position above text

#qr_cutout_z = -1.25  # Ensure it sits correctly inside the cutout
qr_cutout_z = -0.72   # Ensure it sits correctly inside the cutout


# 📌 Adjust for 180° Y-axis rotation
qr_cutout_x_rotated = -qr_cutout_x  # Mirror X-coordinate

# Assemble baseplate & legend
assy_all = cq.Assembly(baseplate_ro, color=cq.Color("lightgray"))

# Add legend
assy_all.add(assy_legend,
    loc=cq.Location((base_length / 2 - leg_length / 2 - 1.5, -base_width / 2 + leg_width / 2 + 1, base_height+0.9), (1, 0, 0), 360)
)

# Add QR Code into the cutout
assy_all.add( assy_qr,
    #loc=cq.Location((qr_cutout_x_rotated, qr_cutout_y, qr_cutout_z), (0, 0, 1), 0)  # Ensures correct placement
    loc=cq.Location((qr_cutout_x_rotated, qr_cutout_y, qr_cutout_z), (0, 1, 0), 180)  # ✅ Rotate 180° around Y-axis
)

In [20]:
# export as .step

In [13]:
print_location_str=print_location.replace(" ","_")
assy_all.save("map_baseplate_full_200_x_200_x_"+ str(base_height) +"-"+ print_location_str+ "_rand24_rechts_qr.step")

/opt/tljh/user/lib/python3.12/site-packages/cadquery/utils.py:39: FutureWarning: save will be removed in the next release.
  warn(f"{f.__name__} will be removed in the next release.", FutureWarning)


In [ ]:
from OCP.STEPControl import STEPControl_Reader
from OCP.TopExp import TopExp_Explorer
#from OCP.TopoDS import TopoDS_Shape
#from OCP.TopAbs import TopAbs_ShapeEnum
#from OCP.BRepMesh import BRepMesh_IncrementalMesh
#from OCP.BRep import BRep_Tool
#from OCP.TopoDS import topods_Face
#import trimesh

def step_to_trimesh(step_file):
    reader = STEPControl_Reader()
    reader.ReadFile(step_file)
    reader.TransferRoots()
    shape = reader.OneShape()

    BRepMesh_IncrementalMesh(shape, 0.1)  # Mesh with deflection=0.1

    faces = TopExp_Explorer(shape, TopAbs_ShapeEnum.TopAbs_FACE)

    meshes = []

    while faces.More():
        face = topods_Face(faces.Current())
        triangulation = BRep_Tool.Triangulation(face, None)

        if triangulation is None:
            faces.Next()
            continue

        nodes = triangulation.Nodes()
        triangles = triangulation.Triangles()

        vertices = [(nodes.Value(i + 1).X(), nodes.Value(i + 1).Y(), nodes.Value(i + 1).Z()) for i in range(nodes.Length())]
        faces_idx = [(tri.Value(1) - 1, tri.Value(2) - 1, tri.Value(3) - 1) for tri in [triangles.Value(i + 1) for i in range(triangles.Length())]]

        mesh = trimesh.Trimesh(vertices=vertices, faces=faces_idx)
        meshes.append(mesh)
        faces.Next()

    return trimesh.util.concatenate(meshes)

# Convert STEP to GLTF
mesh = step_to_trimesh("model.step")
mesh.export("model.glb")  # or "model.gltf"